In [ ]:
import pandas as pd
import numpy as np
import requests
import random
from geopy.geocoders import Nominatim
from IPython.display import Image
from IPython.core.display import HTML
from pandas.io.json import json_normalize
import sklearn.neighbors
from sklearn.cluster import KMeans
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium
import warnings

# Filter out UserWarning
warnings.filterwarnings("ignore", category=UserWarning)


print('Libraries imported.')

Libraries imported.


In [ ]:
columns_to_read = {
    'Fuel Type Code': str,
    'Station Name': str,
    'Street Address': str,
    'City': str,
    'State': str,
    'ZIP': str,
    'EV Level2 EVSE Num': float,  # Change the data type to float
    'EV DC Fast Count': float,    # Change the data type to float
    'Latitude': float,
    'Longitude': float,
    'ID': str,
    'Facility Type': str
}
EVCS = pd.read_csv('Existing_Charging_Stations.csv', usecols=columns_to_read.keys(), dtype=columns_to_read)
EVCS.columns = EVCS.columns.str.replace(' ', '_')
EVCS=EVCS[EVCS['City'] == 'San Jose']

EVCS.head()

Fuel_Type_Code                        Station_Name       Street_Address  \
146           ELEC                      Premier Nissan  1120 W Capitol Expy   
171           ELEC                  Cupertino Electric        1132 N 7th St   
202           ELEC  Homewood Suites - San Jose Airport      10 W Trimble Rd   
510           ELEC                  American Red Cross        2731 N 1st St   
515           ELEC                 Elements Apartments    1201 Parkmoor Ave   

         City State    ZIP  EV_Level2_EVSE_Num  EV_DC_Fast_Count   Latitude  \
146  San Jose    CA  95136                 1.0               2.0  37.275144   
171  San Jose    CA  95112                12.0               NaN  37.362180   
202  San Jose    CA  95131                 2.0               NaN  37.385140   
510  San Jose    CA  95134                 2.0               NaN  37.390356   
515  San Jose    CA  95126                 1.0               NaN  37.317246   

      Longitude     ID Facility_Type  
146 -121.877656  39935    CAR_DEALER  
171 -121.899539  46482       UTILITY  
202 -121.928800  49342         HOTEL  
510 -121.932236  89034   OFFICE_BLDG  
515 -121.909487  89626   PARKING_LOT

In [ ]:
# Create a new 'Charger_Type' column based on 'EV Level2 EVSE Num' 0-DC Charger;1-Level 2 Charger
EVCS['Charger_Type'] = EVCS['EV_Level2_EVSE_Num'].apply(lambda x: 0 if x == 0 else 1)
EVCS['Charger_Type'] = pd.Categorical(EVCS['Charger_Type'])

In [ ]:
EVCS.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 553 entries, 146 to 15198
Data columns (total 13 columns):
 #   Column              Non-Null Count  Dtype   
---  ------              --------------  -----   
 0   Fuel_Type_Code      553 non-null    object  
 1   Station_Name        553 non-null    object  
 2   Street_Address      553 non-null    object  
 3   City                553 non-null    object  
 4   State               553 non-null    object  
 5   ZIP                 553 non-null    object  
 6   EV_Level2_EVSE_Num  524 non-null    float64 
 7   EV_DC_Fast_Count    37 non-null     float64 
 8   Latitude            553 non-null    float64 
 9   Longitude           553 non-null    float64 
 10  ID                  553 non-null    object  
 11  Facility_Type       29 non-null     object  
 12  Charger_Type        553 non-null    category
dtypes: category(1), float64(4), object(8)
memory usage: 56.8+ KB


fsq3WC1BAN5NhQyoZvwkF4rRM1zpSnSzLB9QZpZpZiR4psQ=

In [ ]:
EVCS['EV_Level2_EVSE_Num'].fillna(0, inplace=True)
EVCS['EV_DC_Fast_Count'].fillna(0, inplace=True)
EVCS['Facility_Type'].fillna('NONE', inplace=True)

In [ ]:
EVCS.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 553 entries, 146 to 15198
Data columns (total 13 columns):
 #   Column              Non-Null Count  Dtype   
---  ------              --------------  -----   
 0   Fuel_Type_Code      553 non-null    object  
 1   Station_Name        553 non-null    object  
 2   Street_Address      553 non-null    object  
 3   City                553 non-null    object  
 4   State               553 non-null    object  
 5   ZIP                 553 non-null    object  
 6   EV_Level2_EVSE_Num  553 non-null    float64 
 7   EV_DC_Fast_Count    553 non-null    float64 
 8   Latitude            553 non-null    float64 
 9   Longitude           553 non-null    float64 
 10  ID                  553 non-null    object  
 11  Facility_Type       553 non-null    object  
 12  Charger_Type        553 non-null    category
dtypes: category(1), float64(4), object(8)
memory usage: 56.8+ KB


In [ ]:
! pip install pulp


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.3/14.3 MB 66.1 MB/s eta 0:00:00


In [ ]:
import geopandas as gpd
from pulp import LpProblem, LpVariable, lpSum, LpMaximize
from shapely.geometry import Point
import matplotlib.pyplot as plt
import math

transit_bus_stops = gpd.read_file('bus_stop_point.geojson')
proposed_charging_stations = gpd.GeoDataFrame(columns=['Latitude', 'Longitude', 'Capacity'])

# Extract latitude and longitude from the 'geometry' column
transit_bus_stops['Latitude'] = transit_bus_stops['geometry'].y
transit_bus_stops['Longitude'] = transit_bus_stops['geometry'].x

transit_bus_stops.drop(columns=['geometry'], inplace=True)
# Drop rows with NaN values in the 'name' column
transit_bus_stops = transit_bus_stops.dropna(subset=['name'])


In [ ]:
transit_bus_stops

highway                                   network route_ref  \
2    bus_stop                                    Amtrak       NaN   
3    bus_stop                                    Amtrak       NaN   
10   bus_stop                                       MST       NaN   
12   bus_stop                                       VTA     10;10   
13   bus_stop                                       VTA       181   
..        ...                                       ...       ...   
309       NaN                                       VTA       NaN   
310       NaN                                       VTA       NaN   
311       NaN                                       VTA       NaN   
312       NaN  VTA;Amtrak;MST;BoltBus;Greyhound;Megabus       NaN   
313       NaN                                       NaN       NaN   

                                name public_transport bench  \
2             E San Fernando & S 5th         platform   NaN   
3             E San Fernando & S 5th         platform   NaN   
10          San Fernando & San Pedro              NaN   NaN   
12                Public Bus VTA #10         platform   NaN   
13   Civic Center Light Rail Station              NaN   yes   
..                               ...              ...   ...   
309         Eastridge Transit Center              NaN   NaN   
310                     Santa Teresa          station   NaN   
311                      Valley Fair              NaN   NaN   
312  San José Diridon Transit Center          station   NaN   
313         Alum Rock Transit Center              NaN   NaN   

                                        operator shelter  bus local_ref  ...  \
2                                            NaN     NaN  NaN       NaN  ...   
3                                            NaN     NaN  NaN       NaN  ...   
10                                           NaN     NaN  NaN       NaN  ...   
12   Santa Clara Valley Transportation Authority     NaN  NaN         8  ...   
13                                           NaN     yes  NaN       NaN  ...   
..                                           ...     ...  ...       ...  ...   
309                                          NaN     NaN  NaN       NaN  ...   
310  Santa Clara Valley Transportation Authority     NaN  yes       NaN  ...   
311                                          NaN     NaN  NaN       NaN  ...   
312                                          NaN     NaN  NaN       NaN  ...   
313                                          NaN     NaN  NaN       NaN  ...   

    network:wikidata surface covered  lit                old_name   wikidata  \
2                NaN     NaN     NaN  NaN                     NaN        NaN   
3                NaN     NaN     NaN  NaN                     NaN        NaN   
10               NaN     NaN     NaN  NaN  San Fernando & Almaden        NaN   
12          Q1456861     NaN     NaN  NaN                     NaN        NaN   
13               NaN     NaN     NaN  NaN                     NaN        NaN   
..               ...     ...     ...  ...                     ...        ...   
309              NaN     NaN     NaN  NaN                     NaN  Q14681891   
310              NaN     NaN     NaN  NaN                     NaN   Q7419950   
311              NaN     NaN     NaN  NaN                     NaN        NaN   
312              NaN     NaN     NaN  NaN                     NaN        NaN   
313              NaN     NaN     NaN  NaN                     NaN   Q4737340   

    operator:wikidata                    wikipedia   Latitude   Longitude  
2                 NaN                          NaN  37.336490 -121.884501  
3                 NaN                          NaN  37.336254 -121.885414  
10                NaN                          NaN  37.333168 -121.891784  
12                NaN                          NaN  37.368459 -121.927689  
13                NaN                          NaN  37.351472 -121.902293  
..                ...                     

In [ ]:
!pip install geopy

In [ ]:
import pandas as pd
import numpy as np
from geopy.geocoders import Nominatim
import folium
from sklearn.cluster import KMeans
from sklearn.metrics import pairwise_distances_argmin_min
from sklearn.base import BaseEstimator, ClusterMixin

class CustomKMeans(BaseEstimator, ClusterMixin):
    def __init__(self, n_clusters, existing_locations, penalty_factor=1000, *args, **kwargs):
        self.n_clusters = n_clusters
        self.existing_locations = existing_locations
        self.penalty_factor = penalty_factor
        self.kmeans = KMeans(n_clusters=n_clusters, *args, **kwargs)

    def fit(self, X, y=None, sample_weight=None):
        self.kmeans.fit(X)
        return self

    def transform(self, X):
        distances_to_existing = pairwise_distances_argmin_min(X, self.existing_locations)[1]
        penalties = self.penalty_factor / distances_to_existing
        distances = self.kmeans.transform(X)
        return distances + penalties[:, np.newaxis]

    def fit_transform(self, X, y=None, **fit_params):
        self.fit(X, **fit_params)
        return self.transform(X)

In [ ]:
# Filter data to keep only charging stations within SJ
san_jose_coords = (37.3541, -121.9552)
radius = 15  # Radius in km to filter around SJ

def is_within_radius(location, center, radius):
    R = 6371  # Earth's radius in km
    lat1, lon1 = np.radians(location)
    lat2, lon2 = np.radians(center)

    dlat = lat2 - lat1
    dlon = lon2 - lon1

    a = np.sin(dlat/2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon/2)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1-a))

    distance = R * c
    return distance <= radius

EVCS = EVCS[EVCS.apply(lambda row: is_within_radius((row['Latitude'], row['Longitude']), san_jose_coords, radius), axis=1)]

In [ ]:
P = 25  # Number of new charging stations

# Get the latitude and longitude coordinates of transit bus stops
transit_bus_stop_coordinates = transit_bus_stops[['Latitude', 'Longitude']].values
transit_bus_stop_names = transit_bus_stops['name'].values  # Get the names of transit bus stops

# Initialize k-means clustering with random centers at the coordinates of transit bus stops
init_centers = transit_bus_stop_coordinates[np.random.choice(len(transit_bus_stop_coordinates), P, replace=False)]

existing_locations = np.array(list(EVCS[['Latitude', 'Longitude']].values))
# Run the custom k-means clustering algorithm
kmeans = CustomKMeans(n_clusters=P, random_state=0, init=init_centers, n_init=1, existing_locations=existing_locations).fit(init_centers)

# Create a map centered on San Jose, California
map_ = folium.Map(location=san_jose_coords, zoom_start=12)

# Add existing charging station locations to the map
for _, row in EVCS.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Station_Name'], icon=folium.Icon(color='green', icon='plug', prefix='fa')).add_to(map_)

# Add new charging station locations to the map, ensuring they are within transit bus stops
for i, center_idx in enumerate(kmeans.kmeans.labels_):
    center = kmeans.kmeans.cluster_centers_[center_idx]

    # Check if the new charging station location is within the coordinates of transit bus stops
    is_within_transit_stops = np.isclose(transit_bus_stop_coordinates, center).all(axis=1)

    if is_within_transit_stops.any():
        charging_station_name = transit_bus_stop_names[is_within_transit_stops][0]
        popup_content = f'<span style="font-size: 12px; font-weight: bold;">Location :<br>{charging_station_name}</span>'
        folium.Marker(location=center, popup=popup_content, icon=folium.Icon(color='blue', icon='bus', prefix='fa')).add_to(map_)

# Save the map to an HTML file
map_.save('charging_stations_map.html')

# Print the new charging station coordinates
for i, center in enumerate(kmeans.kmeans.cluster_centers_):
    print(f"New charging station {i + 1} at: {center}")


New charging station 1 at: [  37.3109779 -121.8846996]
New charging station 2 at: [  37.3838384 -121.8968707]
New charging station 3 at: [  37.3362544 -121.8854141]
New charging station 4 at: [  37.4034506 -121.9030684]
New charging station 5 at: [  37.3579807 -121.8326691]
New charging station 6 at: [  37.3514724 -121.9022928]
New charging station 7 at: [  37.3438025 -121.8747442]
New charging station 8 at: [  37.3501374 -121.8269015]
New charging station 9 at: [  37.3319376 -121.9122127]
New charging station 10 at: [  37.2899015 -121.8872396]
New charging station 11 at: [  37.2368194 -121.789417 ]
New charging station 12 at: [  37.368459  -121.9276886]
New charging station 13 at: [  37.2218949 -121.8729549]
New charging station 14 at: [  37.3414674 -121.8203194]
New charging station 15 at: [  37.3198612 -121.877276 ]
New charging station 16 at: [  37.3682414 -121.9272621]
New charging station 17 at: [  37.3518506 -121.9020993]
New charging station 18 at: [  37.3269868 -121.9005148]
N

Data Collection: Gather data on existing charging stations (EVCS), transit bus stops (transit_bus_stops), and any relevant constraints or criteria.

Linear Programming Optimization: Use Linear Programming (LP) with PuLP to find an initial set of optimized charging station locations while considering constraints such as coverage, proximity to existing stations, and other specific requirements.

Clustering: Apply a clustering algorithm (e.g., K-means) to group the optimized locations into clusters based on geographical proximity, ensuring efficient deployment.

Cluster Center Refinement: Refine the number of charging stations within each cluster, if needed, to balance station distribution.

Final Suggested Locations: The centers of the clusters, along with any refinements, represent the final suggested charging station locations, strategically chosen to meet coverage and deployment goals.

This process combines linear programming optimization and clustering to identify optimal charging station locations that maximize coverage and efficiently address specific constraints.

In [ ]:
# Save the map to an HTML file
map_.save('charging_stations_map.html')

# Display the map within the notebook
display(map_)

In [ ]:
school = pd.read_csv('School.csv')

In [ ]:

school.head()

FCN  Ca  Nbr                                Terminal Name  \
0  73513    46800  ALUM ROCK UNION ELEMENTARY  SCHOOL DISTRICT   
1  78171    51148              BERRYESSA UNION SCHOOL DISTRICT   
2  24079    50088          CAMPBELL UNION HIGH SCHOOL DISTRICT   
3  72274    46797          EASTSIDE UNION HIGH SCHOOL DISTRICT   
4  43300    48083                    EVERGREEN SCHOOL DISTRICT   

                    Address      City State    Zip  Latitude  Longitude  
0           2930 GAY AVENUE  SAN JOSE    CA  95127  37.37384 -121.79316  
1         945 PIEDMONT ROAD  SAN JOSE    CA  95132  37.40898 -121.82790  
2        2225 CAMDEN AVENUE  SAN JOSE    CA  95124  37.25545 -121.92535  
3  830 NORTH CAPITOL AVENUE  SAN JOSE    CA  95133  37.37164 -121.86119  
4          2976 FOWLER ROAD  SAN JOSE    CA  95135  37.27582 -121.71464

In [ ]:
# Create a map centered on San Jose, California
map_ = folium.Map(location=san_jose_coords, zoom_start=12)

# Add existing charging station locations to the map
for _, row in EVCS.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Station_Name'], icon=folium.Icon(color='green', icon='plug', prefix='fa')).add_to(map_)
for _, row in school.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Terminal Name'], icon=folium.Icon(color='orange', icon='bus', prefix='fa')).add_to(map_)
map_.save('SchoolBus_charging_stations_map.html')
display(map_)

Key points along delivery routes to ensure that trucks can charge during their stops or breaks.

In [ ]:
import folium
import numpy as np
import pandas as pd
from sklearn.cluster import KMeans
from geopy.geocoders import Nominatim
import time

# Create a function to get the address from coordinates using Geoapify
def get_address_from_coords(lat, lon):
    geolocator = Nominatim(user_agent="charging_station_locator")
    location = geolocator.reverse(f"{lat}, {lon}", exactly_one=True)
    if location is not None:
        return location.address
    else:
        return "Address not found"

P = 25  # Number of new charging stations

# Get the latitude and longitude coordinates of existing charging stations
existing_charging_station_coordinates = EVCS[['Latitude', 'Longitude']].values

# Initialize k-means clustering with random centers at the coordinates of existing charging stations
init_centers = existing_charging_station_coordinates[np.random.choice(len(existing_charging_station_coordinates), P, replace=False)]

# Provide an array of existing charging station coordinates
existing_locations = np.array(list(EVCS[['Latitude', 'Longitude']].values))

# Run the custom k-means clustering algorithm
kmeans = CustomKMeans(n_clusters=P, random_state=0, init=init_centers, n_init=1, existing_locations=existing_locations).fit(init_centers)

# Create a map centered on San Jose, California
map_ = folium.Map(location=san_jose_coords, zoom_start=12)

# Add existing charging station locations to the map
for _, row in EVCS.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Station_Name'], icon=folium.Icon(color='green', icon='plug', prefix='fa')).add_to(map_)

# Add new charging station locations to the map
for i, center in enumerate(kmeans.kmeans.cluster_centers_):
    address = get_address_from_coords(center[0], center[1])
    popup_content = f'<span style="font-size: 12px; font-weight: bold;">New Charging Station {i + 1}</span><br>{address}'
    folium.Marker(location=center, popup=popup_content, icon=folium.Icon(color='purple', icon='truck', prefix='fa')).add_to(map_)

# Save the map to an HTML file
map_.save('Delivery_Truck_charging_stations_map.html')

# Print the new charging station coordinates
for i, center in enumerate(kmeans.kmeans.cluster_centers_):
    print(f"New charging station {i + 1} at: {center}")


New charging station 1 at: [  37.407701 -121.953088]
New charging station 2 at: [  37.360123 -121.868415]
New charging station 3 at: [  37.353451 -121.905829]
New charging station 4 at: [  37.24614  -121.873361]
New charging station 5 at: [  37.380271 -121.922277]
New charging station 6 at: [  37.331325 -121.893778]
New charging station 7 at: [  37.319706 -121.87047 ]
New charging station 8 at: [  37.300233 -121.824873]
New charging station 9 at: [  37.411488 -121.950264]
New charging station 10 at: [  37.366384 -121.919634]
New charging station 11 at: [  37.384869 -121.924531]
New charging station 12 at: [  37.35242 -121.90709]
New charging station 13 at: [  37.374063 -121.896233]
New charging station 14 at: [  37.413264 -121.941164]
New charging station 15 at: [  37.412635 -121.942287]
New charging station 16 at: [  37.366992 -121.873409]
New charging station 17 at: [  37.374022 -121.895912]
New charging station 18 at: [  37.247256 -121.874416]
New charging station 19 at: [  37.36932

In [ ]:
display(map_)

In [ ]:
import numpy as np
# Save the new charging station coordinates to a CSV file
np.savetxt('charging_station_coordinates.csv', kmeans.kmeans.cluster_centers_, delimiter=',', header='Latitude,Longitude', comments='')

# You can load the coordinates from this file in the future using:
# Load the coordinates from the CSV file, skipping the header row
coordinates = np.loadtxt('charging_station_coordinates.csv', delimiter=',', skiprows=1)

In [ ]:
P = 55  # Number of new charging stations

# Get the latitude and longitude coordinates of transit bus stops
transit_bus_stop_coordinates = transit_bus_stops[['Latitude', 'Longitude']].values
transit_bus_stop_names = transit_bus_stops['name'].values  # Get the names of transit bus stops

# Initialize k-means clustering with random centers at the coordinates of transit bus stops
init_centers = transit_bus_stop_coordinates[np.random.choice(len(transit_bus_stop_coordinates), P, replace=False)]

existing_locations = np.array(list(EVCS[['Latitude', 'Longitude']].values))
# Run the custom k-means clustering algorithm
kmeans = CustomKMeans(n_clusters=P, random_state=0, init=init_centers, n_init=1, existing_locations=existing_locations).fit(init_centers)

# Create a map centered on San Jose, California
map_ = folium.Map(location=san_jose_coords, zoom_start=12)

# Add existing charging station locations to the map
for _, row in EVCS.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Station_Name'], icon=folium.Icon(color='green', icon='plug', prefix='fa')).add_to(map_)

# Add new charging station locations to the map, ensuring they are within transit bus stops
for i, center_idx in enumerate(kmeans.kmeans.labels_):
    center = kmeans.kmeans.cluster_centers_[center_idx]

    # Check if the new charging station location is within the coordinates of transit bus stops
    is_within_transit_stops = np.isclose(transit_bus_stop_coordinates, center).all(axis=1)

    if is_within_transit_stops.any():
        charging_station_name = transit_bus_stop_names[is_within_transit_stops][0]
        popup_content = f'<span style="font-size: 12px; font-weight: bold;">Location :<br>{charging_station_name}</span>'
        folium.Marker(location=center, popup=popup_content, icon=folium.Icon(color='blue', icon='bus', prefix='fa')).add_to(map_)

# Add new charging station locations to the map, for delivery trucks
for i, center in enumerate(kmeans.kmeans.cluster_centers_):
    address = get_address_from_coords(center[0], center[1])
    popup_content = f'<span style="font-size: 12px; font-weight: bold;">New Charging Station {i + 1}</span><br>{address}'
    folium.Marker(location=center, popup=popup_content, icon=folium.Icon(color='purple', icon='truck', prefix='fa')).add_to(map_)

# Add new charging station locations to the map, for dschool Bus
for _, row in school.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Terminal Name'], icon=folium.Icon(color='orange', icon='bus', prefix='fa')).add_to(map_)

# Save the map to an HTML file
map_.save('charging_stations_map.html')
display(map_)

In [ ]:
# Add existing charging station locations to the map
for _, row in EVCS.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Station_Name'], icon=folium.Icon(color='green', icon='plug', prefix='fa')).add_to(map_)
import numpy as np
np.random.seed(42)
# Create a new DataFrame with 35 random rows from transit_bus_stops
transit_bus_stops = transit_bus_stops.sample(n=35)
# Add new charging station locations to the map, ensuring they are within transit bus stops
for _, row in transit_bus_stops.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['name'], icon=folium.Icon(color='blue', icon='bus', prefix='fa')).add_to(map_)
# Add new charging station locations to the map, for delivery trucks
for i, center in enumerate(kmeans.kmeans.cluster_centers_):
    address = get_address_from_coords(center[0], center[1])
    popup_content = f'<span style="font-size: 12px; font-weight: bold;">New Charging Station {i + 1}</span><br>{address}'
    folium.Marker(location=center, popup=popup_content, icon=folium.Icon(color='purple', icon='truck', prefix='fa')).add_to(map_)
# Add new charging station locations to the map, for dschool Bus
for _, row in school.iterrows():
    folium.Marker(location=[row['Latitude'], row['Longitude']], popup=row['Terminal Name'], icon=folium.Icon(color='orange', icon='bus', prefix='fa')).add_to(map_)
# Save the map to an HTML file
map_.save('charging_stations_map.html')
display(map_)